In [1]:
import numpy as np
import pandas as pd
pd.options.display.max_columns = None
pd.options.display.max_rows = None

import matplotlib.pyplot as plt
%matplotlib inline

import datetime as dt
import pickle
import os
import time

import seaborn as sns
sns.set()
from matplotlib import style
# style.use('ggplot')
%load_ext autoreload
%autoreload 2

In [2]:
df = pd.read_csv('sp500_wti.csv')
df['Date'] = pd.to_datetime(df['Date'])
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1197718 entries, 0 to 1197717
Data columns (total 34 columns):
 #   Column                     Non-Null Count    Dtype         
---  ------                     --------------    -----         
 0   Date                       1197718 non-null  datetime64[ns]
 1   Adj Close                  1197718 non-null  float64       
 2   volume_obv                 1197718 non-null  float64       
 3   volume_fi                  1197718 non-null  float64       
 4   volatility_bbm             1197718 non-null  float64       
 5   volatility_bbw             1197718 non-null  float64       
 6   volatility_bbhi            1197718 non-null  float64       
 7   volatility_bbli            1197718 non-null  float64       
 8   trend_macd                 1197718 non-null  float64       
 9   trend_macd_signal          1197718 non-null  float64       
 10  trend_macd_diff            1197718 non-null  float64       
 11  trend_psar_up_indicator    1197718 no

In [3]:
def cat_cont_split(df, maxcard=55, omit_vars=['Date', 'Adj Close', 'Return', 'target_return']):
    """Helper function that returns column names of categorical & continuous features from df."""
    cat_feats, cont_feats = [], []
    for col in df:
        if col in omit_vars: 
            continue
        if (df[col].dtype==int or df[col].dtype==float) and df[col].unique().shape[0] > maxcard:
            cont_feats.append(col)
        else:
            cat_feats.append(col)
    return cat_feats, cont_feats
    
cat_vars, cont_vars = cat_cont_split(df)
print(len(cat_vars), 'Categorical Features:')
print(cat_vars)
print(len(cont_vars), 'Continuous Features:')
print(cont_vars)

19 Categorical Features:
['volatility_bbhi', 'volatility_bbli', 'trend_psar_up_indicator', 'trend_psar_down_indicator', 'ticker', 'exchange', 'sector', 'industry', 'Year', 'Month', 'Week', 'Day', 'Dayofweek', 'Is_month_end', 'Is_month_start', 'Is_quarter_end', 'Is_quarter_start', 'Is_year_end', 'Is_year_start']
11 Continuous Features:
['volume_obv', 'volume_fi', 'volatility_bbm', 'volatility_bbw', 'trend_macd', 'trend_macd_signal', 'trend_macd_diff', 'momentum_ao', 'momentum_roc', 'Dayofyear', 'Elapsed']


In [4]:
class Categorifier:
    ''' Transform categorical features into category types '''
    def apply_train(self, df, cat_vars):
        self.cat_vars = cat_vars
        self.categories = {}
        for v in self.cat_vars:
            df.loc[:, v] = df.loc[:, v].astype('category').cat.as_ordered()
            self.categories[v] = df[v].cat.categories
            
    def apply_test(self, df_test):
        for v in self.cat_vars:
            df_test.loc[:, v] = pd.Categorical(df[v], categories=self.categories[v], ordered=True)

cat = Categorifier()
cat.apply_train(df, cat_vars)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1197718 entries, 0 to 1197717
Data columns (total 34 columns):
 #   Column                     Non-Null Count    Dtype         
---  ------                     --------------    -----         
 0   Date                       1197718 non-null  datetime64[ns]
 1   Adj Close                  1197718 non-null  float64       
 2   volume_obv                 1197718 non-null  float64       
 3   volume_fi                  1197718 non-null  float64       
 4   volatility_bbm             1197718 non-null  float64       
 5   volatility_bbw             1197718 non-null  float64       
 6   volatility_bbhi            1197718 non-null  category      
 7   volatility_bbli            1197718 non-null  category      
 8   trend_macd                 1197718 non-null  float64       
 9   trend_macd_signal          1197718 non-null  float64       
 10  trend_macd_diff            1197718 non-null  float64       
 11  trend_psar_up_indicator    1197718 no

In [5]:
# class Normalizer:
#     ''' Normalize continuous features '''
#     def apply_train(self, df, cont_vars, by_var='ticker'):
#         ''' compute mean & std of continous columns to normalize them '''
#         self.cont_vars = cont_vars
#         groups = df[cont_vars+[by_var]].groupby(by_var)
#         self.means = groups.mean()
#         self.stds = groups.std()
#         df = df.merge(self.means, on='ticker', suffixes=["", "_mean"])
#         df = df.merge(self.stds, on='ticker', suffixes=["", "_std"])
#         for v in cont_vars:
#             df[v] = (df[v] - df[v+"_mean"]) / (df[v+"_std"] + 1e-7)
#         df = df.loc[:, ~df.columns.str.contains("_mean")]
#         df = df.loc[:, ~df.columns.str.contains("_std")]
#         return df
            
#     def apply_test(self, df_test):
#         df_test = df_test.merge(self.means, on='ticker', suffixes=["", "_mean"])
#         df_test = df_test.merge(self.stds, on='ticker', suffixes=["", "_std"])
#         for v in cont_vars:
#             df_test[v] = (df_test[v] - df_test[v+"_mean"]) / (df_test[v+"_std"] + 1e-7)
#         df_test = df_test.loc[:, ~df_test.columns.str.contains("_mean")]
#         df_test = df_test.loc[:, ~df_test.columns.str.contains("_std")]
#         return df_test 
    
# norm = Normalizer()
# df = norm.apply_train(df, cont_vars)
df.describe()

Adj Close    volume_obv     volume_fi  volatility_bbm  \
count  1.197718e+06  1.197718e+06  1.197718e+06    1.197718e+06   
mean   2.591268e+00  7.303894e+01  1.843599e-05    2.315740e+00   
std    2.318143e+00  5.691948e+02  6.169358e-01    2.165420e+00   
min    1.140688e-01 -2.179233e+04 -2.253191e+02    1.071531e-01   
25%    1.296095e+00  7.519720e+00 -3.691836e-03    1.200374e+00   
50%    1.967868e+00  3.641876e+01  6.343970e-04    1.732195e+00   
75%    3.098650e+00  7.559374e+01  5.133156e-03    2.673131e+00   
max    5.483901e+01  2.438403e+04  1.216110e+02    5.273659e+01   

       volatility_bbw    trend_macd  trend_macd_signal  trend_macd_diff  \
count    1.197718e+06  1.197718e+06       1.197718e+06     1.197718e+06   
mean     2.399355e-01  8.452663e-03       8.466540e-03     1.277652e-04   
std      3.745992e-01  6.712947e-02       6.300806e-02     2.031146e-02   
min      0.000000e+00 -2.367287e+00      -2.048775e+00    -1.112718e+00   
25%      9.376011e-02 -1.102848e-02      -9.943336e-03    -5.117796e-03   
50%      1.511008e-01  6.766243e-03       6.660563e-03     2.658306e-04   
75%      2.606259e-01  2.512427e-02       2.405540e-02     5.605973e-03   
max      2.088635e+01  2.726452e+00       2.488435e+00     1.231475e+00   

        momentum_ao  momentum_roc        Return  target_return     Dayofyear  \
count  1.197718e+06  1.197718e+06  1.197718e+06   1.197718e+06  1.197718e+06   
mean   1.784300e-02  6.953162e-01  6.006663e-02   5.977433e-02  1.819516e+02   
std    1.697995e-01  5.748798e+00  1.732757e+00   1.732488e+00  1.054133e+02   
min   -6.488795e+00 -5.931778e+01 -6.189338e+01  -6.189338e+01  2.000000e+00   
25%   -2.941598e-02 -2.364635e+00 -7.458466e-01  -7.459848e-01  9.000000e+01   
50%    1.459041e-02  7.744420e-01  7.058580e-02   7.039026e-02  1.820000e+02   
75%    6.025717e-02  3.787397e+00  8.851387e-01   8.848415e-01  2.740000e+02   
max    7.642687e+00  1.104421e+02  6.190656e+01   6.190656e+01  3.660000e+02   

            Elapsed  
count  1.197718e+06  
mean   1.424747e+09  
std    9.181067e+07  
min    1.262650e+09  
25%    1.345680e+09  
50%    1.426205e+09  
75%    1.504051e+09  
max    1.581984e+09

In [6]:
last_day = df['Date'].max()
cut_day = last_day + dt.timedelta(-90)
train_df = df[df['Date'] <= cut_day].sort_values(by='Date', ascending=False).reset_index(drop=True)
test_df = df[(df['Date'] > cut_day) & (df['Date'] < last_day)].sort_values(by='Date', ascending=False).reset_index(drop=True)
train_df.shape, test_df.shape, train_df.Date.min(), train_df.Date.max(), test_df.Date.min(), test_df.Date.max()

((1169210, 34),
 (28025, 34),
 Timestamp('2010-01-05 00:00:00'),
 Timestamp('2019-11-20 00:00:00'),
 Timestamp('2019-11-21 00:00:00'),
 Timestamp('2020-02-14 00:00:00'))

In [7]:
from stage1_model import *

In [8]:
dep_var = 'target_return'
cont_vars = cont_vars + ['Return']
cat_sz = [(nc, len(df[nc].cat.categories)+1) for nc in cat_vars]
# emb_szs = [(nc, min(50, (nc+1)//2)) for _, nc in cat_sz]
emb_szs = [(nc, min(50, round(1.6*nc**0.56))) for _, nc in cat_sz]

In [9]:
model = Stage1Model(emb_szs, len(cont_vars), hidden_sizes=[1024, 512],
                    emb_dropout = 0.1, dropout_prob = [0.001, .01], use_bn=True)
# hidden_sizes=[1024, 512], emb_dropout=0., 
#                       dropout_prob=0., use_bn=True, out_size=1)

[167, 1024, 512, 1]
0 4
1 4
2 4


In [10]:
from torch.utils.data import DataLoader
train_ds = Stage1Dataset(train_df, dep_var, cat_vars, cont_vars)
test_ds = Stage1Dataset(test_df, dep_var, cat_vars, cont_vars)
train_dl = DataLoader(train_ds, 128, shuffle=True)

In [11]:
print(model)

Stage1Model(
  (embeds): ModuleList(
    (0): Embedding(3, 3)
    (1): Embedding(3, 3)
    (2): Embedding(3, 3)
    (3): Embedding(3, 3)
    (4): Embedding(486, 51)
    (5): Embedding(3, 3)
    (6): Embedding(13, 7)
    (7): Embedding(105, 22)
    (8): Embedding(12, 6)
    (9): Embedding(13, 7)
    (10): Embedding(54, 15)
    (11): Embedding(32, 11)
    (12): Embedding(6, 4)
    (13): Embedding(3, 3)
    (14): Embedding(3, 3)
    (15): Embedding(3, 3)
    (16): Embedding(3, 3)
    (17): Embedding(3, 3)
    (18): Embedding(2, 2)
  )
  (emb_dropout): Dropout(p=0.1, inplace=False)
  (bn_cont): BatchNorm1d(12, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (layers): Sequential(
    (0): Linear(in_features=167, out_features=1024, bias=True)
    (1): ReLU(inplace=True)
    (2): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (3): Dropout(p=0.001, inplace=False)
    (4): Linear(in_features=1024, out_features=512, bias=True)
    (5): ReL

In [12]:
# t0 = time.time()
# train_model(model, train_dl, n_epochs=2, lr=1e-4)
# # print(time.time() - t0)

In [13]:
# t0 = time.time()
train_model(model, train_dl, n_epochs=2, lr=1e-3, weight_decay=0.2)
train_model(model, train_dl, n_epochs=2, lr=3e-4, weight_decay=0.2)
train_model(model, train_dl, n_epochs=2, lr=1e-4, weight_decay=0.2)
train_model(model, train_dl, n_epochs=2, lr=1e-5, weight_decay=0.2)
# train_model(model, train_dl, n_epochs=2, lr=3e-4)#, one_cycle=False)
# print(time.time() - t0)

  0%|          | 9/9135 [00:00<01:44, 87.61it/s]

Epoch 1: training loss=3.028


  0%|          | 9/9135 [00:00<01:45, 86.69it/s]

Epoch 2: training loss=3.021


  0%|          | 9/9135 [00:00<01:42, 89.21it/s]

...

Epoch 2: training loss=3.021


  0%|          | 10/9135 [00:00<01:33, 97.44it/s]

Epoch 1: training loss=3.022


100%|██████████| 9135/9135 [00:53<00:00, 172.29it/s]

Epoch 2: training loss=3.021


In [31]:
PATH = './models/stage0_no_norm.pth'
# PATH = './models/tmp.pth'
saved = torch.load(PATH)
if set(saved.keys()) == {'model', 'opt'}:  ## fastai saved model
    saved = saved['model']
model.load_state_dict(saved)

<All keys matched successfully>

In [32]:
t0 = time.time()
train_preds, train_targets = predict(model, train_ds, 1024)
print(time.time() - t0)
print(np.sum(train_targets[:, 0] != train_df['target_return']))

100%|██████████| 1142/1142 [00:14<00:00, 78.22it/s]


14.610078573226929
0


In [33]:
test_preds, test_targets = predict(model, test_ds, 1024)
print(np.sum(test_targets[:, 0] != test_df['target_return']))

100%|██████████| 28/28 [00:00<00:00, 88.79it/s]

0


In [34]:
test_preds

array([[-0.07857711],
       [ 0.7165676 ],
       [ 0.24467483],
       ...,
       [ 0.8539822 ],
       [ 2.213164  ],
       [ 0.951283  ]], dtype=float32)

In [35]:
def MAE(y, y_hat):
    return np.mean(np.abs(y_hat-y))

def MAPE(y, y_hat):
    return np.mean(np.abs(y_hat-y) / (y+1e-3)) * 100

def RMSE(y, y_hat):
    return np.sqrt(np.mean((y_hat - y)**2))

def RMSPE(y, y_hat):
    return np.sqrt(np.mean(((y - y_hat) / (y+1e-3)) ** 2))

def scores(y, y_hat):
    return [MAE(y, y_hat), MAPE(y, y_hat), RMSE(y, y_hat), RMSPE(y, y_hat)]

train_scores = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(train_targets, train_preds)))
print('Training metrics:', train_scores)
test_scores = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(test_targets, test_preds)))
print('Test metrics:', test_scores)

Training metrics: {'MAE': 1.3250093141043824, 'MAPE': 402.1061484214423, 'RMSE': 1.889986867988357, 'RMSPE': 66.1819595029508}
Test metrics: {'MAE': 1.1843014301463, 'MAPE': 389.3664065833323, 'RMSE': 1.666889232903563, 'RMSPE': 67.11912908090332}


In [69]:
def MAE(y, y_hat):
    return np.mean(np.abs(y_hat-y))

def MAPE(y, y_hat):
    return np.mean(np.abs(y_hat-y) / (y+1e-3)) * 100

def RMSE(y, y_hat):
    return np.sqrt(np.mean((y_hat - y)**2))

def RMSPE(y, y_hat):
    return np.sqrt(np.mean(((y - y_hat) / (y+1e-3)) ** 2))

def scores(y, y_hat):
    return [MAE(y, y_hat), MAPE(y, y_hat), RMSE(y, y_hat), RMSPE(y, y_hat)]

train_scores = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(train_targets, train_preds)))
print('Training metrics:', train_scores)
test_scores = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(test_targets, test_preds)))
print('Test metrics:', test_scores)

Training metrics: {'MAE': 1.1728287077374333, 'MAPE': 30.974166905846445, 'RMSE': 1.7382186205476828, 'RMSPE': 4.821718632919006}
Test metrics: {'MAE': 1.0100932719802178, 'MAPE': 29.786151261042114, 'RMSE': 1.47743255050145, 'RMSPE': 4.5887812602497355}


In [57]:
train_dates = train_df.Date.unique()
test_dates = test_df.Date.unique()

is_sorted = lambda A : np.all(A[:-1] > A[1:])
is_sorted(train_dates), is_sorted(test_dates)

(True, True)

In [ ]:
tickers = df.ticker.unique().tolist()
# test_metrics = pd.DataFrame(columns=['ticker', 'MAE', 'MAPE', 'RMSE', 'RMSPE'])
train_metrics, test_metrics = [], []
train_preds_df = pd.DataFrame(index=train_dates)
test_preds_df = pd.DataFrame(index=test_dates)

for i, ticker in enumerate(tickers):
#     print("\n##### {} {}:".format(i, ticker))
    ## Training Metrics
    idx = train_df[train_df.ticker==ticker].index
#     y = train_df.iloc[idx]['target_return'].values
#     yhat = train_preds[idx].numpy().flatten()
    pred_temp = pd.DataFrame(yhat, index=train_df.iloc[idx, 'Date'], columns=[ticker])
    train_preds_df = pd.merge(train_preds_df, pred_temp)
#     train_preds_df[ticker] = yhat
    temp = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(y, yhat)))
    temp['ticker'] = ticker
    train_metrics.append(temp)
    ## Test Metrics
    idx = test_df[test_df.ticker==ticker].index
    yhat = test_preds[idx].numpy().flatten()
    y = test_df.iloc[idx]['target_return'].values
    test_preds_df[ticker] = yhat
    temp = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(y, yhat)))
    temp['ticker'] = ticker
    test_metrics.append(temp)
train_metrics = pd.DataFrame(train_metrics)
test_metrics = pd.DataFrame(test_metrics)
# print(test_metrics)

In [29]:
test_preds.shape, test_targets.shape

((28025, 1), (28025, 1))

In [70]:
tickers = df.ticker.unique().tolist()
train_metrics, test_metrics = [], []
train_preds_df = pd.DataFrame(index=train_dates)
test_preds_df = pd.DataFrame(index=test_dates)
t0 = time.time()
for i, ticker in enumerate(tickers):
    print("\n##### {} {}:".format(i, ticker))
    ## Training Metrics
    idx = train_df[train_df.ticker==ticker].index
    yhat, y = train_preds[idx], train_targets[idx]
    temp = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(y, yhat)))
    temp['ticker'] = ticker
    train_metrics.append(temp)
    
    dates = train_df.iloc[idx]['Date']
    df_temp = pd.DataFrame(train_preds[idx], index=dates, columns=[ticker])
    train_preds_df = train_preds_df.join(df_temp) 
    
    print("Training: ", temp)
    ## Test Metrics
    idx = test_df[test_df.ticker==ticker].index
    yhat, y = test_preds[idx], test_targets[idx]
    temp = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(y, yhat)))
    temp['ticker'] = ticker
    test_metrics.append(temp)
    
    dates = test_df.iloc[idx]['Date']
    df_temp = pd.DataFrame(test_preds[idx], index=dates, columns=[ticker])
    test_preds_df = test_preds_df.join(df_temp) 
    
    print("Testing: ", temp)
    if i % 50 == 0:
        print("Elapsed: ", time.time() - t0)
#     print('-'*20)

train_metrics = pd.DataFrame(train_metrics)
test_metrics = pd.DataFrame(test_metrics)


##### 0 A:
Training:  {'MAE': 1.241837542444216, 'MAPE': 25.950281362065763, 'RMSE': 1.7679201232902355, 'RMSPE': 4.42035518970255, 'ticker': 'A'}
Testing:  {'MAE': 0.8397448713575923, 'MAPE': 10.591695709322952, 'RMSE': 1.0547622986199845, 'RMSPE': 1.0086080282438197, 'ticker': 'A'}
Elapsed:  0.015225410461425781

##### 1 AAL:
Training:  {'MAE': 2.045508776875289, 'MAPE': 33.952139704474924, 'RMSE': 2.8425721394373, 'RMSPE': 4.7827391927872815, 'ticker': 'AAL'}
Testing:  {'MAE': 1.8495619642368386, 'MAPE': 3.866312540742488, 'RMSE': 2.3359282373463306, 'RMSPE': 0.9910407311915462, 'ticker': 'AAL'}

##### 2 AAP:
Training:  {'MAE': 1.1769833960399092, 'MAPE': 7.949832727355864, 'RMSE': 1.8444790335219305, 'RMSPE': 3.4059813743472116, 'ticker': 'AAP'}
Testing:  {'MAE': 1.3336202093980378, 'MAPE': -27.467168536818626, 'RMSE': 1.8028021339315563, 'RMSPE': 1.4547403805065175, 'ticker': 'AAP'}

##### 3 AAPL:
Training:  {'MAE': 1.1632566957568327, 'MAPE': -2.6579087341291627, 'RMSE': 1.62873

Training:  {'MAE': 0.8622948450931713, 'MAPE': 38.30147834080598, 'RMSE': 1.2426583258979944, 'RMSPE': 5.256340956893946, 'ticker': 'ALL'}
Testing:  {'MAE': 0.6906519658416902, 'MAPE': 12.254526724516994, 'RMSE': 0.9188784690999539, 'RMSPE': 1.1732623717606145, 'ticker': 'ALL'}

##### 29 ALLE:
Training:  {'MAE': 0.965460366705114, 'MAPE': 28.288190508397832, 'RMSE': 1.318564956209537, 'RMSPE': 4.479644164457, 'ticker': 'ALLE'}
Testing:  {'MAE': 0.8770431606439903, 'MAPE': 98.37104272842619, 'RMSE': 1.116231305077775, 'RMSPE': 7.089664699290935, 'ticker': 'ALLE'}

##### 30 ALXN:
Training:  {'MAE': 1.6311220475930321, 'MAPE': 5.227457826865821, 'RMSE': 2.257863133137848, 'RMSPE': 3.0583111547205886, 'ticker': 'ALXN'}
Testing:  {'MAE': 1.480824433806505, 'MAPE': -26.69641093172266, 'RMSE': 2.0667257835579416, 'RMSPE': 1.2090288665371272, 'ticker': 'ALXN'}

##### 31 AMAT:
Training:  {'MAE': 1.3927060005556424, 'MAPE': 63.319738903321046, 'RMSE': 1.9116593970688611, 'RMSPE': 6.2405120462811

Testing:  {'MAE': 1.0680407994382035, 'MAPE': -10.448355160709028, 'RMSE': 1.4259602870737413, 'RMSPE': 1.0817319323235186, 'ticker': 'BLL'}

##### 69 BMY:
Training:  {'MAE': 0.9994791049187045, 'MAPE': 34.63917599325808, 'RMSE': 1.4610821213424443, 'RMSPE': 5.025620572312971, 'ticker': 'BMY'}
Testing:  {'MAE': 0.9690712360519783, 'MAPE': 99.20935847288749, 'RMSE': 1.2186513473670193, 'RMSPE': 7.097588657030014, 'ticker': 'BMY'}

##### 70 BR:
Training:  {'MAE': 0.910848663722098, 'MAPE': 36.93411007765634, 'RMSE': 1.2813127043714487, 'RMSPE': 5.26505598960082, 'ticker': 'BR'}
Testing:  {'MAE': 0.8747911346050686, 'MAPE': -6.9381234484582155, 'RMSE': 1.4550817140906507, 'RMSPE': 1.0701274970513728, 'ticker': 'BR'}

##### 71 BSX:
Training:  {'MAE': 1.2656802667998217, 'MAPE': 141.38806758467814, 'RMSE': 1.8081767856394078, 'RMSPE': 9.02303442044336, 'ticker': 'BSX'}
Testing:  {'MAE': 0.8989512161126653, 'MAPE': -23.432819999805332, 'RMSE': 1.3421974666407048, 'RMSPE': 1.1740537327029075,

Testing:  {'MAE': 1.5676226254215058, 'MAPE': -1.881056510533272, 'RMSE': 2.0732648451807933, 'RMSPE': 1.0005891120417856, 'ticker': 'COG'}

##### 107 COO:
Training:  {'MAE': 1.075963506229434, 'MAPE': 16.02030952881694, 'RMSE': 1.5743398367628516, 'RMSPE': 3.7338859380904754, 'ticker': 'COO'}
Testing:  {'MAE': 0.7081243932485263, 'MAPE': 6.662338462591732, 'RMSE': 0.9254506416608431, 'RMSPE': 1.1212490697327575, 'ticker': 'COO'}

##### 108 COP:
Training:  {'MAE': 1.2424415650041487, 'MAPE': 26.83779724558819, 'RMSE': 1.7146726538462946, 'RMSPE': 4.676466686113287, 'ticker': 'COP'}
Testing:  {'MAE': 1.0328977476545846, 'MAPE': 159.14945975157818, 'RMSE': 1.4511300459052072, 'RMSPE': 10.002116597579684, 'ticker': 'COP'}

##### 109 COST:
Training:  {'MAE': 0.8107050877407811, 'MAPE': 16.972102068154662, 'RMSE': 1.147124601309009, 'RMSPE': 4.362539653264218, 'ticker': 'COST'}
Testing:  {'MAE': 0.6459084725533432, 'MAPE': -6.87414134135088, 'RMSE': 0.8244499409176311, 'RMSPE': 1.0778984997

Testing:  {'MAE': 0.5267740444372591, 'MAPE': 21.74672088270023, 'RMSE': 0.6609125147890099, 'RMSPE': 0.9853758930644244, 'ticker': 'DUK'}

##### 142 DVA:
Training:  {'MAE': 1.0276214292887882, 'MAPE': 7.659989640585871, 'RMSE': 1.543545698774792, 'RMSPE': 3.412610351245392, 'ticker': 'DVA'}
Testing:  {'MAE': 0.9617862849430809, 'MAPE': 2.673441512710256, 'RMSE': 1.4388645778257925, 'RMSPE': 1.09915753350824, 'ticker': 'DVA'}

##### 143 DVN:
Training:  {'MAE': 1.675342279109221, 'MAPE': 19.696211904140068, 'RMSE': 2.3261399402983725, 'RMSPE': 4.282942083715772, 'ticker': 'DVN'}
Testing:  {'MAE': 1.8556664776478933, 'MAPE': 183.6484773620264, 'RMSE': 2.3398830163806847, 'RMSPE': 9.97140849678726, 'ticker': 'DVN'}

##### 144 DXC:
Training:  {'MAE': 1.294797981586233, 'MAPE': 24.477352184372783, 'RMSE': 2.296886686683009, 'RMSPE': 4.397047105626012, 'ticker': 'DXC'}
Testing:  {'MAE': 1.641780266020083, 'MAPE': -17.58710181724715, 'RMSE': 2.0610083560134314, 'RMSPE': 1.0195915407378875, 't

...

Training:  {'MAE': 1.087933689416504, 'MAPE': 15.851074603293227, 'RMSE': 1.5041801208654226, 'RMSPE': 3.986073441329393, 'ticker': 'NVR'}
Testing:  {'MAE': 1.1308575579461224, 'MAPE': 2.7005381102393, 'RMSE': 1.4239308387914895, 'RMSPE': 1.006582946588393, 'ticker': 'NVR'}

##### 337 NWL:
Training:  {'MAE': 1.2709065424633286, 'MAPE': 50.40727633413008, 'RMSE': 2.0138886810573178, 'RMSPE': 5.864690756233395, 'ticker': 'NWL'}
Testing:  {'MAE': 1.414593345995334, 'MAPE': -4.3918136902050025, 'RMSE': 1.732896905220045, 'RMSPE': 1.0108280279800534, 'ticker': 'NWL'}

##### 338 NWS:
Training:  {'MAE': 1.083133115640143, 'MAPE': 335.08607660543976, 'RMSE': 1.5180277817258399, 'RMSPE': 13.58549427989042, 'ticker': 'NWS'}
Testing:  {'MAE': 1.0474817849758165, 'MAPE': 279.183806717178, 'RMSE': 1.3362476226549747, 'RMSPE': 12.194809723467111, 'ticker': 'NWS'}

##### 339 NWSA:
Training:  {'MAE': 1.1067849699986343, 'MAPE': 157.63088823455493, 'RMSE': 1.5670160336879144, 'RMSPE': 9.542347780444027

Training:  {'MAE': 0.9064367168528946, 'MAPE': -2.827071499817885, 'RMSE': 1.2473935379487548, 'RMSPE': 2.5182454079523016, 'ticker': 'PSA'}
Testing:  {'MAE': 0.6175735118886381, 'MAPE': 12.324119551445401, 'RMSE': 0.7803343999217269, 'RMSPE': 1.550340911736293, 'ticker': 'PSA'}

##### 369 PSX:
Training:  {'MAE': 1.183005524310071, 'MAPE': 26.501814157552513, 'RMSE': 1.6070834104281835, 'RMSPE': 4.376400020798055, 'ticker': 'PSX'}
Testing:  {'MAE': 1.0715858994324925, 'MAPE': -34.41113078010496, 'RMSE': 1.5373251331895132, 'RMSPE': 1.3808835673876896, 'ticker': 'PSX'}

##### 370 PVH:
Training:  {'MAE': 1.4486261088838643, 'MAPE': 15.5335290614434, 'RMSE': 2.109729868180822, 'RMSPE': 3.879376413184986, 'ticker': 'PVH'}
Testing:  {'MAE': 1.444490463582914, 'MAPE': -16.01387758625744, 'RMSE': 1.8659808586578697, 'RMSPE': 1.175388997247052, 'ticker': 'PVH'}

##### 371 PWR:
Training:  {'MAE': 1.2779830709848583, 'MAPE': 39.63880808317974, 'RMSE': 1.899286169786649, 'RMSPE': 5.13117566872314

Testing:  {'MAE': 0.753451899622815, 'MAPE': 100.99923037228587, 'RMSE': 0.97521290293701, 'RMSPE': 7.093261290055918, 'ticker': 'SLG'}

##### 400 SNA:
Training:  {'MAE': 1.0278657976262124, 'MAPE': 6.631028592801792, 'RMSE': 1.4688274529947167, 'RMSPE': 3.2682388389532826, 'ticker': 'SNA'}
Testing:  {'MAE': 0.8608908943956983, 'MAPE': -19.450108576015296, 'RMSE': 1.0856611519331245, 'RMSPE': 1.1423981599488107, 'ticker': 'SNA'}
Elapsed:  8.201061725616455

##### 401 SNPS:
Training:  {'MAE': 0.9053856570435985, 'MAPE': 52.830661077373605, 'RMSE': 1.2753091107244685, 'RMSPE': 5.770853681404254, 'ticker': 'SNPS'}
Testing:  {'MAE': 1.1252123115582855, 'MAPE': 13.112673094638613, 'RMSE': 1.4449262961169633, 'RMSPE': 1.0280015769654074, 'ticker': 'SNPS'}

##### 402 SO:
Training:  {'MAE': 0.6813042021313277, 'MAPE': 70.83171413895043, 'RMSE': 0.9107454166063491, 'RMSPE': 6.778047996446598, 'ticker': 'SO'}
Testing:  {'MAE': 0.695109341810471, 'MAPE': 5.751458576398802, 'RMSE': 0.9035925199010

Testing:  {'MAE': 1.4785293514837146, 'MAPE': 8.563393855844396, 'RMSE': 2.509708363751162, 'RMSPE': 0.9611280303323323, 'ticker': 'TWTR'}

##### 432 TXN:
Training:  {'MAE': 1.1174589919156641, 'MAPE': 55.10781723717862, 'RMSE': 1.5527830107804328, 'RMSPE': 5.874048669645491, 'ticker': 'TXN'}
Testing:  {'MAE': 1.1317389004637624, 'MAPE': -2.749716597625622, 'RMSE': 1.4850893755752292, 'RMSPE': 1.2407671195946062, 'ticker': 'TXN'}

##### 433 TXT:
Training:  {'MAE': 1.3652578615360278, 'MAPE': 34.54585872806904, 'RMSE': 2.002842113484901, 'RMSPE': 5.019669987051567, 'ticker': 'TXT'}
Testing:  {'MAE': 1.1727420513344151, 'MAPE': 73.81781630161072, 'RMSE': 1.8091457209351673, 'RMSPE': 7.104724510119082, 'ticker': 'TXT'}

##### 434 UA:
Training:  {'MAE': 1.9382041029276957, 'MAPE': 47.71821204648701, 'RMSE': 3.2912922129641085, 'RMSPE': 5.903948289445106, 'ticker': 'UA'}
Testing:  {'MAE': 1.8507951337565336, 'MAPE': 285.5082979256925, 'RMSE': 3.0219843220820186, 'RMSPE': 12.19387103865547, 

Training:  {'MAE': 1.1066234077513617, 'MAPE': 10.135557543776368, 'RMSE': 1.5932792765851918, 'RMSPE': 3.7329337677974035, 'ticker': 'WBA'}
Testing:  {'MAE': 0.8898878652908967, 'MAPE': 47.15937375177834, 'RMSE': 1.298916025510098, 'RMSPE': 7.134865696300493, 'ticker': 'WBA'}

##### 461 WDC:
Training:  {'MAE': 1.7599319655306218, 'MAPE': 27.60564612040204, 'RMSE': 2.4882888082404984, 'RMSPE': 4.5427907503715685, 'ticker': 'WDC'}
Testing:  {'MAE': 1.9318146966930003, 'MAPE': -5.188814058260063, 'RMSE': 2.3766490036957224, 'RMSPE': 1.211294065553933, 'ticker': 'WDC'}

##### 462 WEC:
Training:  {'MAE': 0.7735621078561064, 'MAPE': 29.57678799958523, 'RMSE': 1.0259062074576553, 'RMSPE': 4.679113568089119, 'ticker': 'WEC'}
Testing:  {'MAE': 0.5937468172150058, 'MAPE': 121.25551946740876, 'RMSE': 0.7485958892199098, 'RMSPE': 7.078635499849563, 'ticker': 'WEC'}

##### 463 WELL:
Training:  {'MAE': 0.9568076093414336, 'MAPE': 39.83984936415739, 'RMSE': 1.3368359120623754, 'RMSPE': 5.14490578567

In [49]:
# test_df.iloc[idx][['Date', 'target_return']]
test_preds_df.T

2020-02-14  2020-02-13  2020-02-12  2020-02-11  2020-02-10  2020-02-07  \
A        0.407824    1.164651    0.192518    0.142287    1.521680    1.276204   
AAL      0.647052    0.748164    0.044937    0.262176    1.119142    1.104943   
AAP     -0.082039    1.284139    0.652970   -0.337780    1.416506    0.732949   
AAPL    -0.126678    0.365233    0.019726    0.080690    0.528975    0.409795   
ABBV     0.041746    0.722966    0.240080    0.001581    1.082921    0.394847   
ABC      0.000195    0.520092    0.261865   -0.053428    0.556677    0.478094   
ABMD     0.307312    0.367455    0.533098    0.111702    0.478066    0.233357   
ABT      0.176663    1.150567    0.352162   -0.208344    1.679024    0.968651   
ACN      0.594953    0.476294    0.369894   -0.167175    0.775342    0.484108   
ADBE     0.314999   -0.050603   -0.019330    0.003030    0.349375    0.578879   
ADI      0.211594    0.903953    0.077447    0.053532    1.581016    1.294460   
ADM      0.308031    0.913292    0.618764    0.765524    0.800581    0.868638   
ADP     -0.065342    0.051410   -0.199454   -0.156098    0.682642    0.906258   
ADS      0.895500    0.595401    0.326506    0.035480    1.028608    0.784477   
ADSK    -0.217349   -0.086162   -0.095450   -0.076312    0.303245    0.537930   
AEE      0.144584    0.854260    0.463307    0.655643    0.915958    1.020690   
AEP      0.309431    0.543912    0.372931    0.127908    0.541328    0.819207   
AES      0.277991    0.513620    0.250227    0.132140    0.682214    0.793748   
AFL      0.529664    0.673702   -0.621099    0.025316    1.036484    1.290469   
AGN      0.195923    0.287181    0.314713    0.128782    0.478608    0.151919   
AIG      0.317239    0.964976   -0.411274    0.165071    1.064080    0.933491   
AIV      0.113611    0.912476    0.608574    0.326030    0.664569    0.980379   
AIZ     -0.101731    0.155373   -0.088531    0.057048    0.574192    0.942488   
AJG      0.403074   -0.104713    0.208316   -0.075411    0.204596    0.365333   
AKAM     0.234741    0.250541    0.225063    0.248057    0.671772    0.669469   
ALB      0.083816    0.924634    0.372869    0.072496    1.036821    1.145947   
ALGN     0.030819    1.032115    0.695380   -0.070927    1.586108    0.842457   
ALK      0.310399    0.953884   -0.145916   -0.310837    1.614003    1.062818   
ALL     -0.167841    0.360279   -0.025093    0.048929    0.528688    0.706072   
ALLE    -0.102860    0.740771    0.426455    0.492996    0.429224    0.660171   
ALXN     0.454547    0.966863    0.391191    0.301172    1.212877    0.953116   
AMAT     0.116010    0.486320   -0.320781   -0.263071    1.096151    1.305643   
AMD     -0.062478    0.456725   -0.122856   -0.064654    0.955171    0.783021   
AME      0.409993    1.129929    0.560376    0.549005    1.857498    1.097382   
AMG      0.194541    1.007283   -0.117818    0.075544    1.087689    1.318524   
AMGN     0.278303    0.830962    0.486448    0.201812    1.102120    0.773794   
AMP      0.231019    0.591149   -0.195753   -0.023568    0.893600    0.692947   
AMT      0.034590    0.824562    0.330107    0.415650    0.760337    0.946585   
AMZN     0.263495   -0.030690    0.201912   -0.016934    0.225246    0.144315   
ANET     0.723385    0.822204    0.518015    0.445589    0.675802    0.944697   
ANSS     0.252506    0.449260    0.128902    0.050747    0.895804    0.706809   
ANTM     0.404796    1.199188    0.657250    0.193502    1.451353    0.987803   
AON      0.325422   -0.144811    0.149556    0.213520    0.332702    0.494143   
AOS      0.590005    1.250228    0.142366    0.221879    1.850089    1.462512   
APA      0.302496    1.489596    0.390864    0.587179    1.543727    1.284655   
APD     -0.045753    1.046176    0.050462   -0.540724    1.339857    0.854588   
APH      0.512507    0.394825    0.494844    0.388896    0.421437    0.932237   
APTV     0.339518    1.027789    0.431211    0.410336    1.194845    1.081346   
ARE     -0.120127    1.211650    0.436

In [44]:
ticker = 'AMZN'
idx = test_df[test_df.ticker==ticker].index
dates = test_df.iloc[idx]['Date']
df_temp = pd.DataFrame(test_preds[idx], index=dates, columns=[ticker])
df_temp

AMZN
Date                
2020-02-14  0.263495
2020-02-13 -0.030690
2020-02-12  0.201912
2020-02-11 -0.016934
2020-02-10  0.225246
2020-02-07  0.144315
2020-02-06  0.392106
2020-02-05  0.997427
2020-02-04 -0.184375
2020-02-03 -0.035895
2020-01-31  0.243459
2020-01-30  0.583905
2020-01-29 -0.202870
2020-01-28  0.347849
2020-01-27 -0.272868
2020-01-24  0.669178
2020-01-23 -0.231572
2020-01-22  0.026126
2020-01-21  0.589946
2020-01-17  0.195542
2020-01-16  0.484902
2020-01-15  0.867575
2020-01-14  0.247601
2020-01-13  0.134124
2020-01-10  1.321201
2020-01-09  0.528532
2020-01-08  0.458562
2020-01-07 -0.401491
2020-01-06  0.269755
2020-01-03 -0.106243
2020-01-02  0.499381
2019-12-31  1.041293
2019-12-30  0.218685
2019-12-27 -0.175525
2019-12-26 -0.313418
2019-12-24  0.221958
2019-12-23 -0.640877
2019-12-20 -0.732589
2019-12-19  0.035382
2019-12-18  0.346178
2019-12-17  0.819429
2019-12-16  0.290757
2019-12-13 -0.141338
2019-12-12  0.749419
2019-12-11 -0.268072
2019-12-10 -1.474964
2019-12-09  0.082017
2019-12-06  0.215054
2019-12-05  0.243943
2019-12-04  1.405727
2019-12-03  0.379515
2019-12-02  0.858154
2019-11-29 -0.123118
2019-11-27 -0.218058
2019-11-26  0.476950
2019-11-25  1.386238
2019-11-22 -2.190174
2019-11-21  0.703795

In [36]:
tickers = df.ticker.unique().tolist()
train_metrics, test_metrics = [], []
train_preds_df = pd.DataFrame(index=train_dates)
test_preds_df = pd.DataFrame(index=test_dates)
t0 = time.time()
for i, ticker in enumerate(tickers):
    print("\n##### {} {}:".format(i, ticker))
    ## Training Metrics
    idx = train_df[train_df.ticker==ticker].index
    yhat, y = train_preds[idx], train_targets[idx]
    temp = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(y, yhat)))
    temp['ticker'] = ticker
    train_metrics.append(temp)
    
    dates = train_df.iloc[idx]['Date']
    df_temp = pd.DataFrame(train_preds[idx], index=dates, columns=[ticker])
    train_preds_df = train_preds_df.join(df_temp) 
    
    print("Training: ", temp)
    ## Test Metrics
    idx = test_df[test_df.ticker==ticker].index
    yhat, y = test_preds[idx], test_targets[idx]
    temp = dict(zip(['MAE', 'MAPE', 'RMSE', 'RMSPE'], scores(y, yhat)))
    temp['ticker'] = ticker
    test_metrics.append(temp)
    
    dates = test_df.iloc[idx]['Date']
    df_temp = pd.DataFrame(test_preds[idx], index=dates, columns=[ticker])
    test_preds_df = test_preds_df.join(df_temp) 
    
    print("Testing: ", temp)
    if i % 50 == 0:
        print("Elapsed: ", time.time() - t0)
#     print('-'*20)

train_metrics = pd.DataFrame(train_metrics)
test_metrics = pd.DataFrame(test_metrics)


##### 0 A:
Training:  {'MAE': 1.4478975855916099, 'MAPE': 477.0840444467563, 'RMSE': 1.9993547452770117, 'RMSPE': 81.26018683751178, 'ticker': 'A'}
Testing:  {'MAE': 1.1148671560402807, 'MAPE': 8.416612165449584, 'RMSE': 1.5474640570957607, 'RMSPE': 6.238863164946472, 'ticker': 'A'}
Elapsed:  0.015609264373779297

##### 1 AAL:
Training:  {'MAE': 2.18205034408238, 'MAPE': 461.6163058221002, 'RMSE': 2.9987156201125296, 'RMSPE': 70.92950384232513, 'ticker': 'AAL'}
Testing:  {'MAE': 2.0131705338471515, 'MAPE': 20.741686729461208, 'RMSE': 2.517444545572768, 'RMSPE': 2.1046515407193844, 'ticker': 'AAL'}

##### 2 AAP:
Training:  {'MAE': 1.394866113787816, 'MAPE': 341.5507048856792, 'RMSE': 2.0547810935993684, 'RMSPE': 77.38724366263096, 'ticker': 'AAP'}
Testing:  {'MAE': 1.513748212936626, 'MAPE': -23.791654715303743, 'RMSE': 2.0027639006814133, 'RMSPE': 8.776131542519808, 'ticker': 'AAP'}

##### 3 AAPL:
Training:  {'MAE': 1.2602244938081972, 'MAPE': 39.55932357896448, 'RMSE': 1.733814889233

Training:  {'MAE': 1.1285138235208365, 'MAPE': 507.8648104339859, 'RMSE': 1.54119126178736, 'RMSPE': 64.37000636357469, 'ticker': 'ALL'}
Testing:  {'MAE': 0.7916182470430546, 'MAPE': 116.46529080112774, 'RMSE': 0.9772639630184691, 'RMSPE': 7.596106645273455, 'ticker': 'ALL'}

##### 29 ALLE:
Training:  {'MAE': 1.0489752890042978, 'MAPE': 265.08085015860763, 'RMSE': 1.4154332901830942, 'RMSPE': 36.96043613365964, 'ticker': 'ALLE'}
Testing:  {'MAE': 0.8589694034726065, 'MAPE': 1121.1042552320664, 'RMSE': 1.1051659182608347, 'RMSPE': 87.51695587906971, 'ticker': 'ALLE'}

##### 30 ALXN:
Training:  {'MAE': 1.7149593053275518, 'MAPE': 73.32052596201356, 'RMSE': 2.3413578618810864, 'RMSPE': 31.203559450993577, 'ticker': 'ALXN'}
Testing:  {'MAE': 1.5069747161725369, 'MAPE': -115.05815423637995, 'RMSE': 2.1494741055979176, 'RMSPE': 8.612124340852942, 'ticker': 'ALXN'}

##### 31 AMAT:
Training:  {'MAE': 1.5657402511889464, 'MAPE': 898.2305763990929, 'RMSE': 2.0848601637261934, 'RMSPE': 102.389494

Testing:  {'MAE': 1.2165217968191429, 'MAPE': -104.10656384150683, 'RMSE': 1.5564858515164364, 'RMSPE': 10.058013939363795, 'ticker': 'BLL'}

##### 69 BMY:
Training:  {'MAE': 1.1146534527902805, 'MAPE': 475.41223917599734, 'RMSE': 1.5723085294134296, 'RMSPE': 77.37506349201519, 'ticker': 'BMY'}
Testing:  {'MAE': 1.0997036225562347, 'MAPE': 98.77276227881089, 'RMSE': 1.3617226803586677, 'RMSPE': 8.167543349923806, 'ticker': 'BMY'}

##### 70 BR:
Training:  {'MAE': 0.9908237140856109, 'MAPE': 230.09439743444804, 'RMSE': 1.3679422886747616, 'RMSPE': 31.23993126631153, 'ticker': 'BR'}
Testing:  {'MAE': 0.9411483256211004, 'MAPE': -7.616012658460396, 'RMSE': 1.470169649717396, 'RMSPE': 3.8427490127294512, 'ticker': 'BR'}

##### 71 BSX:
Training:  {'MAE': 1.3334832705670103, 'MAPE': 1191.9199145972523, 'RMSE': 1.8659698134379663, 'RMSPE': 99.79411840045368, 'ticker': 'BSX'}
Testing:  {'MAE': 1.0876873018177686, 'MAPE': -168.01353058494593, 'RMSE': 1.5683744637633104, 'RMSPE': 6.94238037269048

Testing:  {'MAE': 1.243691139794533, 'MAPE': -110.0606548924716, 'RMSE': 1.576948013055701, 'RMSPE': 10.579763522383907, 'ticker': 'COF'}

##### 106 COG:
Training:  {'MAE': 1.7899962422809348, 'MAPE': 520.0970375463309, 'RMSE': 2.440941385517374, 'RMSPE': 72.97475217315852, 'ticker': 'COG'}
Testing:  {'MAE': 1.8066476784466043, 'MAPE': 0.8208747136718516, 'RMSE': 2.3694465231702684, 'RMSPE': 3.335015238765775, 'ticker': 'COG'}

##### 107 COO:
Training:  {'MAE': 1.2821175733240298, 'MAPE': 419.4518232689699, 'RMSE': 1.8103245927357812, 'RMSPE': 80.32308508634695, 'ticker': 'COO'}
Testing:  {'MAE': 0.8621168470488128, 'MAPE': -73.28272794693153, 'RMSE': 1.1229887799837528, 'RMSPE': 5.750695221496645, 'ticker': 'COO'}

##### 108 COP:
Training:  {'MAE': 1.348668371725532, 'MAPE': 250.55780515353652, 'RMSE': 1.825010950409191, 'RMSPE': 40.38718477858765, 'ticker': 'COP'}
Testing:  {'MAE': 1.3660141674266035, 'MAPE': 961.0160871242506, 'RMSE': 1.7782096741777587, 'RMSPE': 68.39458308291171, 

Testing:  {'MAE': 0.6509409367647854, 'MAPE': 2010.4574776226332, 'RMSE': 0.791648487924093, 'RMSPE': 144.8957061962995, 'ticker': 'DRE'}

##### 139 DRI:
Training:  {'MAE': 1.2442316259143054, 'MAPE': 345.9873558109613, 'RMSE': 1.7257875921389443, 'RMSPE': 67.32761016312952, 'ticker': 'DRI'}
Testing:  {'MAE': 0.9926439174607978, 'MAPE': 19.124178639569696, 'RMSE': 1.4189066572870654, 'RMSPE': 1.8307100311217304, 'ticker': 'DRI'}

##### 140 DTE:
Training:  {'MAE': 0.8920911148115902, 'MAPE': 193.3437678741144, 'RMSE': 1.1807255944055322, 'RMSPE': 34.62440182575245, 'ticker': 'DTE'}
Testing:  {'MAE': 0.5587607361329995, 'MAPE': -49.95140416226041, 'RMSE': 0.7199319314486654, 'RMSPE': 6.745429010943152, 'ticker': 'DTE'}

##### 141 DUK:
Training:  {'MAE': 0.873997287839939, 'MAPE': 934.8925636756594, 'RMSE': 1.1581254646200292, 'RMSPE': 90.62954631722103, 'ticker': 'DUK'}
Testing:  {'MAE': 0.6556657856805834, 'MAPE': 49.086743126172685, 'RMSE': 0.8023177205228994, 'RMSPE': 5.82670304526925

...

Training:  {'MAE': 1.1180026999482322, 'MAPE': 547.2500751090334, 'RMSE': 1.5218133358419312, 'RMSPE': 114.31928520146985, 'ticker': 'PM'}
Testing:  {'MAE': 0.9450670757214422, 'MAPE': -226.24075471478983, 'RMSE': 1.1831841315199063, 'RMSPE': 17.717641423736286, 'ticker': 'PM'}

##### 361 PNC:
Training:  {'MAE': 1.1899075361952198, 'MAPE': 265.91364977567434, 'RMSE': 1.621791390219738, 'RMSPE': 39.272216650521784, 'ticker': 'PNC'}
Testing:  {'MAE': 0.9822540319234331, 'MAPE': -33.5676073658714, 'RMSE': 1.2895999808086047, 'RMSPE': 2.684339092166475, 'ticker': 'PNC'}

##### 362 PNR:
Training:  {'MAE': 1.3747949202759175, 'MAPE': 598.355709757761, 'RMSE': 1.8527830313370495, 'RMSPE': 84.1690906442192, 'ticker': 'PNR'}
Testing:  {'MAE': 1.0781535036929588, 'MAPE': 13.105334043468195, 'RMSE': 1.3473676983353273, 'RMSPE': 9.080310364558878, 'ticker': 'PNR'}

##### 363 PNW:
Training:  {'MAE': 0.9634317917431663, 'MAPE': 515.2030652527466, 'RMSE': 1.263403059893104, 'RMSPE': 68.1497939629959,

Testing:  {'MAE': 1.012284266166814, 'MAPE': 424.24341667461, 'RMSE': 1.3103737073508623, 'RMSPE': 39.91631278864712, 'ticker': 'SBUX'}

##### 393 SCHW:
Training:  {'MAE': 1.5338413314945556, 'MAPE': 728.6944503729618, 'RMSE': 2.0463330440341543, 'RMSPE': 95.37676564705981, 'ticker': 'SCHW'}
Testing:  {'MAE': 1.435854687135012, 'MAPE': 2089.9091005466476, 'RMSE': 1.780348083634759, 'RMSPE': 120.75346054528617, 'ticker': 'SCHW'}

##### 394 SEE:
Training:  {'MAE': 1.4340461318332718, 'MAPE': 695.7974699939065, 'RMSE': 1.9547687374740998, 'RMSPE': 109.10562658388184, 'ticker': 'SEE'}
Testing:  {'MAE': 1.4169434404670156, 'MAPE': -32.15361879787641, 'RMSE': 1.793804973612415, 'RMSPE': 6.420935381689661, 'ticker': 'SEE'}

##### 395 SHW:
Training:  {'MAE': 1.0787964415629832, 'MAPE': 86.62875213716589, 'RMSE': 1.4752227426149411, 'RMSPE': 30.106316854954965, 'ticker': 'SHW'}
Testing:  {'MAE': 0.9390671932661863, 'MAPE': -36.640398426303726, 'RMSE': 1.1754591742956924, 'RMSPE': 3.850417076977

Training:  {'MAE': 1.1933765394442108, 'MAPE': 198.30523778449464, 'RMSE': 1.598124872837136, 'RMSPE': 38.09188728878898, 'ticker': 'TMO'}
Testing:  {'MAE': 0.9744951936686562, 'MAPE': -6.853921156164041, 'RMSE': 1.3324402958064, 'RMSPE': 3.7318781001013814, 'ticker': 'TMO'}

##### 423 TMUS:
Training:  {'MAE': 1.588876317247974, 'MAPE': 489.3924129562977, 'RMSE': 2.534109775249439, 'RMSPE': 65.98709876438507, 'ticker': 'TMUS'}
Testing:  {'MAE': 1.0906678773225937, 'MAPE': 373.6854113601947, 'RMSE': 1.930316931876399, 'RMSPE': 25.13440275806239, 'ticker': 'TMUS'}

##### 424 TPR:
Training:  {'MAE': 1.5980253200912635, 'MAPE': 257.3915922856042, 'RMSE': 2.2863446040435655, 'RMSPE': 52.307270924237464, 'ticker': 'TPR'}
Testing:  {'MAE': 1.645841467925112, 'MAPE': -28.08282148656931, 'RMSE': 2.0969777221881944, 'RMSPE': 2.949729948698895, 'ticker': 'TPR'}

##### 425 TRIP:
Training:  {'MAE': 1.8660246440016508, 'MAPE': 433.7755648712085, 'RMSE': 2.8663431617731985, 'RMSPE': 85.63891200809698

Testing:  {'MAE': 1.5412174116698387, 'MAPE': -124.46314861488474, 'RMSE': 2.0190363656475383, 'RMSPE': 5.522060531607512, 'ticker': 'VLO'}
Elapsed:  9.65988540649414

##### 451 VMC:
Training:  {'MAE': 1.5558550110728513, 'MAPE': 378.0512487046682, 'RMSE': 2.1494030764833494, 'RMSPE': 82.18731153314819, 'ticker': 'VMC'}
Testing:  {'MAE': 1.1260883715665742, 'MAPE': -160.0735705762952, 'RMSE': 1.589163996836036, 'RMSPE': 14.49100036640721, 'ticker': 'VMC'}

##### 452 VNO:
Training:  {'MAE': 1.1592902737944293, 'MAPE': 192.12016604086224, 'RMSE': 1.5594965374522256, 'RMSPE': 43.639387749967014, 'ticker': 'VNO'}
Testing:  {'MAE': 0.8794600042880308, 'MAPE': -16.637894114546885, 'RMSE': 1.0909440108858028, 'RMSPE': 2.87042792125782, 'ticker': 'VNO'}

##### 453 VRSK:
Training:  {'MAE': 1.0678338463326622, 'MAPE': 796.9423388244958, 'RMSE': 1.4640126967828264, 'RMSPE': 122.8102803385349, 'ticker': 'VRSK'}
Testing:  {'MAE': 0.7470315633852185, 'MAPE': -122.98695416610252, 'RMSE': 0.8999261811

Testing:  {'MAE': 0.8016690574545425, 'MAPE': 267.37057949567554, 'RMSE': 1.0319426753531584, 'RMSPE': 21.31133004000745, 'ticker': 'XRAY'}

##### 479 XRX:
Training:  {'MAE': 1.4036688509742463, 'MAPE': 1353.959427130721, 'RMSE': 1.992282327793859, 'RMSPE': 110.72882444819197, 'ticker': 'XRX'}
Testing:  {'MAE': 1.0500973063675745, 'MAPE': 190.42613840708472, 'RMSE': 1.4636990097071556, 'RMSPE': 15.832190846422058, 'ticker': 'XRX'}

##### 480 XYL:
Training:  {'MAE': 1.185339548610795, 'MAPE': 398.3753663689822, 'RMSE': 1.6021479286436515, 'RMSPE': 48.66971355765667, 'ticker': 'XYL'}
Testing:  {'MAE': 1.0818226588724102, 'MAPE': 11.347775579636782, 'RMSE': 1.5064292532784884, 'RMSPE': 2.418307772044018, 'ticker': 'XYL'}

##### 481 YUM:
Training:  {'MAE': 1.0516220760397064, 'MAPE': 282.6659152098159, 'RMSE': 1.5113320822828302, 'RMSPE': 48.06092811504162, 'ticker': 'YUM'}
Testing:  {'MAE': 0.9877019937013616, 'MAPE': 40.97526680853773, 'RMSE': 1.2929123926270194, 'RMSPE': 4.6663233941045

In [38]:
# test_df.iloc[idx][['Date', 'target_return']]
test_preds_df.T
# train_preds_df.T.head()

2020-02-14  2020-02-13  2020-02-12  2020-02-11  2020-02-10  2020-02-07  \
A        0.407824    1.164651    0.192518    0.142287    1.521680    1.276204   
AAL      0.647052    0.748164    0.044937    0.262176    1.119142    1.104943   
AAP     -0.082039    1.284139    0.652970   -0.337780    1.416506    0.732949   
AAPL    -0.126678    0.365233    0.019726    0.080690    0.528975    0.409795   
ABBV     0.041746    0.722966    0.240080    0.001581    1.082921    0.394847   
ABC      0.000195    0.520092    0.261865   -0.053428    0.556677    0.478094   
ABMD     0.307312    0.367455    0.533098    0.111702    0.478066    0.233357   
ABT      0.176663    1.150567    0.352162   -0.208344    1.679024    0.968651   
ACN      0.594953    0.476294    0.369894   -0.167175    0.775342    0.484108   
ADBE     0.314999   -0.050603   -0.019330    0.003030    0.349375    0.578879   
ADI      0.211594    0.903953    0.077447    0.053532    1.581016    1.294460   
ADM      0.308031    0.913292    0.618764    0.765524    0.800581    0.868638   
ADP     -0.065342    0.051410   -0.199454   -0.156098    0.682642    0.906258   
ADS      0.895500    0.595401    0.326506    0.035480    1.028608    0.784477   
ADSK    -0.217349   -0.086162   -0.095450   -0.076312    0.303245    0.537930   
AEE      0.144584    0.854260    0.463307    0.655643    0.915958    1.020690   
AEP      0.309431    0.543912    0.372931    0.127908    0.541328    0.819207   
AES      0.277991    0.513620    0.250227    0.132140    0.682214    0.793748   
AFL      0.529664    0.673702   -0.621099    0.025316    1.036484    1.290469   
AGN      0.195923    0.287181    0.314713    0.128782    0.478608    0.151919   
AIG      0.317239    0.964976   -0.411274    0.165071    1.064080    0.933491   
AIV      0.113611    0.912476    0.608574    0.326030    0.664569    0.980379   
AIZ     -0.101731    0.155373   -0.088531    0.057048    0.574192    0.942488   
AJG      0.403074   -0.104713    0.208316   -0.075411    0.204596    0.365333   
AKAM     0.234741    0.250541    0.225063    0.248057    0.671772    0.669469   
ALB      0.083816    0.924634    0.372869    0.072496    1.036821    1.145947   
ALGN     0.030819    1.032115    0.695380   -0.070927    1.586108    0.842457   
ALK      0.310399    0.953884   -0.145916   -0.310837    1.614003    1.062818   
ALL     -0.167841    0.360279   -0.025093    0.048929    0.528688    0.706072   
ALLE    -0.102860    0.740771    0.426455    0.492996    0.429224    0.660171   
ALXN     0.454547    0.966863    0.391191    0.301172    1.212877    0.953116   
AMAT     0.116010    0.486320   -0.320781   -0.263071    1.096151    1.305643   
AMD     -0.062478    0.456725   -0.122856   -0.064654    0.955171    0.783021   
AME      0.409993    1.129929    0.560376    0.549005    1.857498    1.097382   
AMG      0.194541    1.007283   -0.117818    0.075544    1.087689    1.318524   
AMGN     0.278303    0.830962    0.486448    0.201812    1.102120    0.773794   
AMP      0.231019    0.591149   -0.195753   -0.023568    0.893600    0.692947   
AMT      0.034590    0.824562    0.330107    0.415650    0.760337    0.946585   
AMZN     0.263495   -0.030690    0.201912   -0.016934    0.225246    0.144315   
ANET     0.723385    0.822204    0.518015    0.445589    0.675802    0.944697   
ANSS     0.252506    0.449260    0.128902    0.050747    0.895804    0.706809   
ANTM     0.404796    1.199188    0.657250    0.193502    1.451353    0.987803   
AON      0.325422   -0.144811    0.149556    0.213520    0.332702    0.494143   
AOS      0.590005    1.250228    0.142366    0.221879    1.850089    1.462512   
APA      0.302496    1.489596    0.390864    0.587179    1.543727    1.284655   
APD     -0.045753    1.046176    0.050462   -0.540724    1.339857    0.854588   
APH      0.512507    0.394825    0.494844    0.388896    0.421437    0.932237   
APTV     0.339518    1.027789    0.431211    0.410336    1.194845    1.081346   
ARE     -0.120127    1.211650    0.436

In [52]:
train_preds_df.shape, test_preds_df.shape

((2488, 485), (58, 485))

In [50]:
# train_df[['Date', 'Return', 'ticker']].T.head()

In [39]:
train_preds_df.T.head()

2019-11-20  2019-11-19  2019-11-18  2019-11-15  2019-11-14  2019-11-13  \
A      -0.173125    0.014028   -1.887160   -0.707659   -0.506079   -0.440797   
AAL    -0.915990   -1.248400   -1.805527   -1.539874    0.355546   -1.217691   
AAP    -1.266273    0.041150   -1.380541   -0.494796   -0.028157   -0.184659   
AAPL   -0.563448    0.059688   -0.994228   -0.325579   -0.234115    0.056112   
ABBV   -0.505165   -0.054685   -0.601865   -0.194781   -0.111602   -0.293036   

      2019-11-12  2019-11-11  2019-11-08  2019-11-07  2019-11-06  2019-11-05  \
A       1.493890   -0.262999    1.083419    0.207876    0.806005    0.284517   
AAL     1.685892    0.166948    0.848828    0.006320    0.289447   -0.561726   
AAP     1.678269   -0.046466    1.162524    0.538126    1.163629    0.126176   
AAPL    0.979335    0.470362    1.110202   -0.126857    0.077007   -0.168604   
ABBV    0.786539   -0.171569    0.731126    0.200423    0.529386   -0.093713   

      2019-11-04  2019-11-01  2019-10-31  2019-10-30  2019-10-29  2019-10-28  \
A       1.267333   -1.193793    0.170246   -2.582492    0.674099   -1.220446   
AAL    -0.159741   -0.741893    0.148914   -2.502535    0.164127   -1.378360   
AAP     1.107906   -1.220052    0.123879   -1.562847    0.499805   -0.535177   
AAPL   -0.497409   -0.473875   -0.025078   -1.004320    0.160406   -0.517604   
ABBV    0.111607   -0.170402    0.115969   -1.405444    0.393109   -0.578264   

      2019-10-25  2019-10-24  2019-10-23  2019-10-22  2019-10-21  2019-10-18  \
A      -0.531646    0.418516   -0.397974    0.130882   -0.953176   -0.844892   
AAL    -0.512470    0.305234   -0.283597   -0.135617   -0.605579   -0.295899   
AAP    -0.156821    0.082611    0.018569   -0.498642   -0.267854   -0.624275   
AAPL   -0.109390    0.263535   -0.132452   -0.079213   -0.424793   -0.143073   
ABBV   -0.057487    0.308040   -0.158104   -0.100776   -0.548239   -0.433061   

      2019-10-17  2019-10-16  2019-10-15  2019-10-14  2019-10-11  2019-10-10  \
A      -0.682608    0.778880   -0.921978    0.223628   -0.324667   -0.486389   
AAL    -0.917815    0.596816   -1.525921    0.300240   -0.655998   -0.290498   
AAP    -0.698815    0.286514   -0.974835   -0.206534   -0.482231   -0.535885   
AAPL   -0.430137    0.317002   -0.679471   -0.221175    0.121447    0.012794   
ABBV   -0.769165    0.578927   -0.825006    0.225841   -0.197594   -0.322581   

      2019-10-09  2019-10-08  2019-10-07  2019-10-04  2019-10-03  2019-10-02  \
A      -0.078974   -0.394212   -0.485216   -0.009816   -0.400843    0.206701   
AAL     0.278652   -0.761731   -0.172229    0.296608   -0.357050   -0.244840   
AAP     0.182961   -0.511598   -0.302772   -0.107913   -0.893276   -0.192483   
AAPL   -0.286079   -0.130338   -0.193990    0.171974   -0.101645    0.147944   
ABBV    0.118637   -0.025405   -0.126986    0.082567   -0.679186    0.070205   

      2019-10-01  2019-09-30  2019-09-27  2019-09-26  2019-09-25  2019-09-24  \
A      -0.054064    0.009957   -0.088281   -0.164737    1.670901   -0.369262   
AAL    -0.121552   -0.283929   -0.599447   -0.115938    1.361616   -1.229549   
AAP    -0.707799    0.062991    0.242749   -0.128250    0.495539   -0.355771   
AAPL   -0.240775    0.326533    0.498160    0.278043    0.967302    0.271359   
ABBV   -0.380549   -0.024914   -0.021678   -0.157548    1.338945    0.241315   

      2019-09-23  2019-09-20  2019-09-19  2019-09-18  2019-09-17  2019-09-16  \
A       0.277692   -0.595866   -1.055457    0.324012    0.171202    0.157092   
AAL     0.040876   -0.433046   -1.255936    0.480317    0.235043    0.030346   
AAP     0.082416   -1.057859   -1.026049    0.231735    0.115828   -0.307661   
AAPL    0.476796   -0.312436   -0.517158    0.382184    0.100654   -0.005523   
ABBV    0.170083   -0.323946   -0.720858    0.268567    0.093381   -0.020248   

      2019-09-13  2019-09-12  2019-09-11  2019-09-10  2019-09-09  2019-09-06  \
A      -0.402009   -0.078020   -0.289836    1.152426   -0.758156   -1.231060  

In [55]:
df[df.ticker=='ABBV']

Date  Adj Close  volume_obv  volume_fi  volatility_bbm  \
10188 2013-01-03   0.991743   -0.215821   0.004217        0.995871   
10189 2013-01-04   0.979214   -1.768135   0.004217        0.990319   
10190 2013-01-07   0.981207   -0.468220   0.004217        0.988041   
10191 2013-01-08   0.959852   -1.765680   0.004217        0.982403   
10192 2013-01-09   0.965262   -0.400155   0.004217        0.979546   
10193 2013-01-10   0.968110    0.737135   0.004217        0.977912   
10194 2013-01-11   0.975313   -0.075734   0.004217        0.976153   
10195 2013-01-14   0.982228    0.765709   0.004217        0.975544   
10196 2013-01-15   0.996922    1.712854   0.004217        0.976509   
10197 2013-01-16   1.024006    2.912216   0.004217        0.979732   
10198 2013-01-17   1.049362    3.959929   0.004217        0.984506   
10199 2013-01-18   1.075293    5.255856   0.004217        0.990516   
10200 2013-01-22   1.049362    4.107555   0.004217        0.993837   
10201 2013-01-23   1.089123    4.905178   0.008092        0.999336   
10202 2013-01-24   1.079327    4.082460   0.005798        1.003541   
10203 2013-01-25   1.083361    4.731404   0.005339        1.007487   
10204 2013-01-28   1.062903    4.212799   0.003079        1.009871   
10205 2013-01-29   1.075005    4.854764   0.003736        1.012633   
10206 2013-01-30   1.064056    4.067294   0.001985        1.014579   
10207 2013-01-31   1.057141    3.288621   0.000941        1.016814   
10208 2013-02-01   1.071259    3.980629   0.002186        1.020159   
10209 2013-02-04   1.074140    4.441701   0.002061        1.024274   
10210 2013-02-05   1.071835    3.912616   0.001595        1.028175   
10211 2013-02-06   1.070107    3.495784   0.001265        1.033058   
10212 2013-02-07   1.049362    2.778717  -0.001016        1.036646   
10213 2013-02-08   1.044464    1.772122  -0.001567        1.039849   
10214 2013-02-11   1.032938    1.333994  -0.002056        1.042696   
10215 2013-02-12   1.020549    0.791152  -0.002712        1.044590   
10216 2013-02-13   1.016227    0.438171  -0.002540        1.045544   
10217 2013-02-14   1.053684    0.988008   0.000731        1.047010   
10218 2013-02-15   1.082784    1.953755   0.004594        1.048662   
10219 2013-02-19   1.100360    2.556076   0.005432        1.049900   
10220 2013-02-20   1.112462    3.144140   0.005661        1.053018   
10221 2013-02-21   1.117360    3.671519   0.005217        1.054413   
10222 2013-02-22   1.108140    3.345369   0.004047        1.055837   
10223 2013-02-25   1.076734    3.006493   0.001966        1.055510   
10224 2013-02-26   1.068666    2.682334   0.001316        1.055794   
10225 2013-02-27   1.058293    1.793425  -0.000173        1.054969   
10226 2013-02-28   1.063768    2.543068   0.000431        1.054954   
10227 2013-03-01   1.089411    3.191634   0.002717        1.056549   
10228 2013-03-04   1.101801    3.585362   0.003018        1.058058   
10229 2013-03-05   1.080767    3.102325   0.001152        1.058386   
10230 2013-03-06   1.087394    3.501042   0.001361        1.059154   
10231 2013-03-07   1.080191    3.178371   0.000838        1.059653   
10232 2013-03-08   1.075869    2.879524   0.000536        1.060962   
10233 2013-03-11   1.085377    3.214681   0.000909        1.062984   
10234 2013-03-12   1.070971    2.740832  -0.000184        1.064863   
10235 2013-03-13   1.070971    3.010343  -0.000158        1.067355   
10236 2013-03-14   1.082208    3.726480   0.001001        1.070615   
10237 2013-03-15   1.109292    4.613202   0.004248        1.073363   
10238 2013-03-18   1.099496    4.237059   0.003121        1.074189   
10239 2013-03-19   1.105258    4.608096   0.002977        1.074431   
10240 2013-03-20   1.125427    5.121820   0.004015        1.075071   
10241 2013-03-21   1.109004    4.777824   0.002643        1.074658   
10242 2013-03-22   1.122834    5.019211   0.002737        1.075384   
10243 2013-03-25   1.132918    5.459729   0.002973        1.078161   
10244 2013-03-26   1.1

In [63]:
# mdt = train_df.Date.min()
k = 0
for i, ticker in enumerate(tickers):
    ## Training Metrics
    dts = train_df[train_df.ticker==ticker].Date
    if min(dts) > train_df.Date.min():
        k += 1
        print("\n##### {} {}:".format(i, ticker))
        print(min(dts))
#     print(min(dts))
print(k)


##### 4 ABBV:
2013-01-03 00:00:00

##### 29 ALLE:
2013-11-19 00:00:00

##### 39 ANET:
2014-06-09 00:00:00

##### 47 APTV:
2011-11-18 00:00:00

##### 79 CBOE:
2010-06-16 00:00:00

##### 84 CDW:
2013-06-28 00:00:00

##### 89 CFG:
2014-09-25 00:00:00

##### 92 CHTR:
2010-01-06 00:00:00

##### 110 COTY:
2013-06-14 00:00:00

##### 168 FANG:
2012-10-15 00:00:00

##### 170 FB:
2012-05-21 00:00:00

##### 171 FBHS:
2011-09-19 00:00:00

##### 181 FLT:
2010-12-16 00:00:00

##### 183 FOX:
2019-03-14 00:00:00

##### 184 FOXA:
2019-03-13 00:00:00

##### 188 FTV:
2016-07-06 00:00:00

##### 194 GM:
2010-11-19 00:00:00

##### 207 HCA:
2011-03-11 00:00:00

##### 212 HII:
2011-03-23 00:00:00

##### 213 HLT:
2013-12-13 00:00:00

##### 218 HPE:
2015-10-20 00:00:00

##### 233 INFO:
2014-06-20 00:00:00

##### 239 IQV:
2013-05-10 00:00:00

##### 256 KEYS:
2014-10-21 00:00:00

##### 257 KHC:
2015-07-07 00:00:00

##### 261 KMI:
2011-02-14 00:00:00

##### 281 LW:
2016-11-11 00:00:00

##### 282 LYB:
2010-04-29 0

In [59]:
mdt

Timestamp('2019-03-14 00:00:00')

In [66]:
train_preds_df.reset_index(drop=False).rename(columns={'index':'Date'}).to_csv('stage1Results/train_preds.csv', index=False)
test_preds_df.reset_index(drop=False).rename(columns={'index':'Date'}).to_csv('stage1Results/test_preds.csv')
train_metrics.to_csv('stage1Results/train_metrics.csv')
test_metrics.to_csv('stage1Results/test_metrics.csv')

In [57]:
train_preds_df.to_csv('stage1Results/train_preds.csv')

In [65]:
temp = train_preds_df.reset_index(drop=False).rename(columns={'index':'Date'})
temp.head()

Date         A       AAL       AAP      AAPL      ABBV       ABC  \
0 2019-11-20 -0.173125 -0.915990 -1.266273 -0.563448 -0.505165 -0.475396   
1 2019-11-19  0.014028 -1.248400  0.041150  0.059688 -0.054685  0.266324   
2 2019-11-18 -1.887160 -1.805527 -1.380541 -0.994228 -0.601865 -1.151644   
3 2019-11-15 -0.707659 -1.539874 -0.494796 -0.325579 -0.194781 -0.003214   
4 2019-11-14 -0.506079  0.355546 -0.028157 -0.234115 -0.111602 -0.096373   

       ABMD       ABT       ACN      ADBE       ADI       ADM       ADP  \
0 -0.170284 -1.061611  0.031242 -0.464184 -0.354372  0.175016 -1.044149   
1 -0.649606 -0.048107  0.325525  0.020812  0.027746  0.201798 -0.161132   
2  1.454538 -1.003759 -1.805057 -1.042933 -1.391701 -0.949091 -0.194746   
3 -0.445357 -0.509085  0.495120 -0.206213 -0.255083 -0.091434 -0.108335   
4 -0.609774 -0.259161  0.703377  0.175646  0.284713 -0.398798 -0.414910   

        ADS      ADSK       AEE       AEP       AES       AFL       AGN  \
0  0.371353 -1.039570 -0.039043  0.138851 -0.063987 -1.103722 -0.244323   
1  0.319347 -0.373862  0.501765  0.202007  0.209188 -0.440346  0.062217   
2 -1.736709 -1.410242 -2.014035 -1.269321 -1.026395 -0.532522 -0.209766   
3  0.780571 -0.598584 -0.905795  0.141177  0.129626 -0.627548 -0.040875   
4  0.653434 -0.875985 -0.205583  0.107397 -0.021624 -0.108798 -0.006298   

        AIG       AIV       AIZ       AJG      AKAM       ALB      ALGN  \
0 -0.709359  0.031519 -0.608879 -0.493599  0.206911 -0.467285 -0.508342   
1  0.031580  0.104040  0.104822  0.231833  0.158091  0.472657 -0.371434   
2 -1.227472 -1.652979 -0.791528 -0.267788 -1.833802 -1.303019 -0.679751   
3 -0.242822 -0.763008 -0.243279  0.173525  0.426259 -0.207301 -1.217838   
4 -0.451925 -0.593988  0.016888 -0.145328  0.727733 -0.291896 -0.394177   

        ALK       ALL      ALLE      ALXN      AMAT       AMD       AME  \
0 -1.474489 -0.469405 -0.853380 -0.379162 -1.108141 -0.755342 -0.725681   
1 -1.605474  0.803091 -0.089807  0.079440  0.139209 -0.305408 -0.679921   
2 -1.761278 -0.712860 -0.797394 -0.486332 -1.233928 -1.158917 -2.433003   
3 -1.758938 -0.128506 -0.374912 -0.162088 -0.511053 -0.314872 -1.019665   
4  0.221998 -0.226512 -0.582603  0.076174 -0.412598 -0.069272 -0.398888   

        AMG      AMGN       AMP       AMT      AMZN      ANET      ANSS  \
0 -0.694651 -0.776903 -0.693320 -0.438066  0.631095 -1.189334 -1.162159   
1  0.216371 -0.025398  0.114671 -0.211680 -0.311048 -0.271658 -0.364683   
2 -0.739825 -0.631909 -0.942853 -1.956205 -1.348709 -1.656941 -2.170841   
3  0.080015 -0.435949  0.018836 -0.883067 -0.593467 -0.561235 -0.778031   
4 -0.042891 -0.355223  0.044673 -0.622956  0.734458  0.397761  0.052583   

       ANTM       AON       AOS       APA       APD       APH      APTV  \
0 -0.500861 -0.641704 -0.142402 -0.980200 -0.831829  0.720244 -0.319645   
1  0.075891  0.071192 -0.668344  0.086140 -0.088537  0.008110  0.000293   
2 -0.754492 -0.920610 -1.243206 -1.159792 -1.228155 -0.108002 -0.964755   
3 -0.214804 -0.094954 -0.628694 -0.607689 -0.212857  0.197316 -0.111310   
4 -0.068852  0.011797  0.119944 -0.878679 -0.883600 -0.094735 -0.198080   

        ARE      ARNC       ATO      ATVI       AVB      AVGO       AVY  \
0 -0.455295 -0.781324 -0.248025 -0.401843  0.347991 -0.712499 -0.579940   
1 -0.113358 -0.019167  0.098219 -0.019326  0.263676 -0.236504 -0.044567   
2 -1.755541 -1.275502 -0.861091 -0.625306 -2.362729 -0.829496 -2.041479   
3 -0.994621 -0.159620 -0.274753  0.210387 -0.495271 -0.518456 -0.671615   
4 -0.815246 -0.605540 -0.174620  0.278142 -0.157929 -0.009724 -0.515737   

        AWK       AXP       AZO        BA       BAC       BAX       BBY  \
0 -0.559700 -0.271509 -0.373694 -0.246048 -0.763364 -1.015478  0.309072   
1 -0.125415  0.049601  0.050814  0.295628 -0.237183  0.028995  0.289860   
2 -1.458163 -0.288827 -1.343239 -0.499365 -1.036820 -1.554965 -1.190913   
3 -0.221569  0.226726 -0.302155 -0.127101  0.235157 -0.289954 -0.297478   
4 -0.331042  0.0074

In [60]:
train_preds_df.head()

A       AAL       AAP      AAPL      ABBV       ABC  \
2019-11-20 -0.173125 -0.915990 -1.266273 -0.563448 -0.505165 -0.475396   
2019-11-19  0.014028 -1.248400  0.041150  0.059688 -0.054685  0.266324   
2019-11-18 -1.887160 -1.805527 -1.380541 -0.994228 -0.601865 -1.151644   
2019-11-15 -0.707659 -1.539874 -0.494796 -0.325579 -0.194781 -0.003214   
2019-11-14 -0.506079  0.355546 -0.028157 -0.234115 -0.111602 -0.096373   

                ABMD       ABT       ACN      ADBE       ADI       ADM  \
2019-11-20 -0.170284 -1.061611  0.031242 -0.464184 -0.354372  0.175016   
2019-11-19 -0.649606 -0.048107  0.325525  0.020812  0.027746  0.201798   
2019-11-18  1.454538 -1.003759 -1.805057 -1.042933 -1.391701 -0.949091   
2019-11-15 -0.445357 -0.509085  0.495120 -0.206213 -0.255083 -0.091434   
2019-11-14 -0.609774 -0.259161  0.703377  0.175646  0.284713 -0.398798   

                 ADP       ADS      ADSK       AEE       AEP       AES  \
2019-11-20 -1.044149  0.371353 -1.039570 -0.039043  0.138851 -0.063987   
2019-11-19 -0.161132  0.319347 -0.373862  0.501765  0.202007  0.209188   
2019-11-18 -0.194746 -1.736709 -1.410242 -2.014035 -1.269321 -1.026395   
2019-11-15 -0.108335  0.780571 -0.598584 -0.905795  0.141177  0.129626   
2019-11-14 -0.414910  0.653434 -0.875985 -0.205583  0.107397 -0.021624   

                 AFL       AGN       AIG       AIV       AIZ       AJG  \
2019-11-20 -1.103722 -0.244323 -0.709359  0.031519 -0.608879 -0.493599   
2019-11-19 -0.440346  0.062217  0.031580  0.104040  0.104822  0.231833   
2019-11-18 -0.532522 -0.209766 -1.227472 -1.652979 -0.791528 -0.267788   
2019-11-15 -0.627548 -0.040875 -0.242822 -0.763008 -0.243279  0.173525   
2019-11-14 -0.108798 -0.006298 -0.451925 -0.593988  0.016888 -0.145328   

                AKAM       ALB      ALGN       ALK       ALL      ALLE  \
2019-11-20  0.206911 -0.467285 -0.508342 -1.474489 -0.469405 -0.853380   
2019-11-19  0.158091  0.472657 -0.371434 -1.605474  0.803091 -0.089807   
2019-11-18 -1.833802 -1.303019 -0.679751 -1.761278 -0.712860 -0.797394   
2019-11-15  0.426259 -0.207301 -1.217838 -1.758938 -0.128506 -0.374912   
2019-11-14  0.727733 -0.291896 -0.394177  0.221998 -0.226512 -0.582603   

                ALXN      AMAT       AMD       AME       AMG      AMGN  \
2019-11-20 -0.379162 -1.108141 -0.755342 -0.725681 -0.694651 -0.776903   
2019-11-19  0.079440  0.139209 -0.305408 -0.679921  0.216371 -0.025398   
2019-11-18 -0.486332 -1.233928 -1.158917 -2.433003 -0.739825 -0.631909   
2019-11-15 -0.162088 -0.511053 -0.314872 -1.019665  0.080015 -0.435949   
2019-11-14  0.076174 -0.412598 -0.069272 -0.398888 -0.042891 -0.355223   

                 AMP       AMT      AMZN      ANET      ANSS      ANTM  \
2019-11-20 -0.693320 -0.438066  0.631095 -1.189334 -1.162159 -0.500861   
2019-11-19  0.114671 -0.211680 -0.311048 -0.271658 -0.364683  0.075891   
2019-11-18 -0.942853 -1.956205 -1.348709 -1.656941 -2.170841 -0.754492   
2019-11-15  0.018836 -0.883067 -0.593467 -0.561235 -0.778031 -0.214804   
2019-11-14  0.044673 -0.622956  0.734458  0.397761  0.052583 -0.068852   

                 AON       AOS       APA       APD       APH      APTV  \
2019-11-20 -0.641704 -0.142402 -0.980200 -0.831829  0.720244 -0.319645   
2019-11-19  0.071192 -0.668344  0.086140 -0.088537  0.008110  0.000293   
2019-11-18 -0.920610 -1.243206 -1.159792 -1.228155 -0.108002 -0.964755   
2019-11-15 -0.094954 -0.628694 -0.607689 -0.212857  0.197316 -0.111310   
2019-11-14  0.011797  0.119944 -0.878679 -0.883600 -0.094735 -0.198080   

                 ARE      ARNC       ATO      ATVI       AVB      AVGO  \
2019-11-20 -0.455295 -0.781324 -0.248025 -0.401843  0.347991 -0.712499   
2019-11-19 -0.113358 -0.019167  0.098219 -0.019326  0.263676 -0.236504   
2019-11-18 -1.755541 -1.275502 -0.861091 -0.625306 -2.362729 -0.829496   
2019-11-15 -0.994621 -0.159620 -0.274753  0.210387 -0.495271 -0.518456   
2019-11-14 -0.815246 -0.605540 -0.174620  0.278142 -0.157929 -0.009724   

              

In [64]:
temp = train_preds_df.copy()
temp.rename(columns={'index':'Date'}).head()

A       AAL       AAP      AAPL      ABBV       ABC  \
2019-11-20 -0.173125 -0.915990 -1.266273 -0.563448 -0.505165 -0.475396   
2019-11-19  0.014028 -1.248400  0.041150  0.059688 -0.054685  0.266324   
2019-11-18 -1.887160 -1.805527 -1.380541 -0.994228 -0.601865 -1.151644   
2019-11-15 -0.707659 -1.539874 -0.494796 -0.325579 -0.194781 -0.003214   
2019-11-14 -0.506079  0.355546 -0.028157 -0.234115 -0.111602 -0.096373   

                ABMD       ABT       ACN      ADBE       ADI       ADM  \
2019-11-20 -0.170284 -1.061611  0.031242 -0.464184 -0.354372  0.175016   
2019-11-19 -0.649606 -0.048107  0.325525  0.020812  0.027746  0.201798   
2019-11-18  1.454538 -1.003759 -1.805057 -1.042933 -1.391701 -0.949091   
2019-11-15 -0.445357 -0.509085  0.495120 -0.206213 -0.255083 -0.091434   
2019-11-14 -0.609774 -0.259161  0.703377  0.175646  0.284713 -0.398798   

                 ADP       ADS      ADSK       AEE       AEP       AES  \
2019-11-20 -1.044149  0.371353 -1.039570 -0.039043  0.138851 -0.063987   
2019-11-19 -0.161132  0.319347 -0.373862  0.501765  0.202007  0.209188   
2019-11-18 -0.194746 -1.736709 -1.410242 -2.014035 -1.269321 -1.026395   
2019-11-15 -0.108335  0.780571 -0.598584 -0.905795  0.141177  0.129626   
2019-11-14 -0.414910  0.653434 -0.875985 -0.205583  0.107397 -0.021624   

                 AFL       AGN       AIG       AIV       AIZ       AJG  \
2019-11-20 -1.103722 -0.244323 -0.709359  0.031519 -0.608879 -0.493599   
2019-11-19 -0.440346  0.062217  0.031580  0.104040  0.104822  0.231833   
2019-11-18 -0.532522 -0.209766 -1.227472 -1.652979 -0.791528 -0.267788   
2019-11-15 -0.627548 -0.040875 -0.242822 -0.763008 -0.243279  0.173525   
2019-11-14 -0.108798 -0.006298 -0.451925 -0.593988  0.016888 -0.145328   

                AKAM       ALB      ALGN       ALK       ALL      ALLE  \
2019-11-20  0.206911 -0.467285 -0.508342 -1.474489 -0.469405 -0.853380   
2019-11-19  0.158091  0.472657 -0.371434 -1.605474  0.803091 -0.089807   
2019-11-18 -1.833802 -1.303019 -0.679751 -1.761278 -0.712860 -0.797394   
2019-11-15  0.426259 -0.207301 -1.217838 -1.758938 -0.128506 -0.374912   
2019-11-14  0.727733 -0.291896 -0.394177  0.221998 -0.226512 -0.582603   

                ALXN      AMAT       AMD       AME       AMG      AMGN  \
2019-11-20 -0.379162 -1.108141 -0.755342 -0.725681 -0.694651 -0.776903   
2019-11-19  0.079440  0.139209 -0.305408 -0.679921  0.216371 -0.025398   
2019-11-18 -0.486332 -1.233928 -1.158917 -2.433003 -0.739825 -0.631909   
2019-11-15 -0.162088 -0.511053 -0.314872 -1.019665  0.080015 -0.435949   
2019-11-14  0.076174 -0.412598 -0.069272 -0.398888 -0.042891 -0.355223   

                 AMP       AMT      AMZN      ANET      ANSS      ANTM  \
2019-11-20 -0.693320 -0.438066  0.631095 -1.189334 -1.162159 -0.500861   
2019-11-19  0.114671 -0.211680 -0.311048 -0.271658 -0.364683  0.075891   
2019-11-18 -0.942853 -1.956205 -1.348709 -1.656941 -2.170841 -0.754492   
2019-11-15  0.018836 -0.883067 -0.593467 -0.561235 -0.778031 -0.214804   
2019-11-14  0.044673 -0.622956  0.734458  0.397761  0.052583 -0.068852   

                 AON       AOS       APA       APD       APH      APTV  \
2019-11-20 -0.641704 -0.142402 -0.980200 -0.831829  0.720244 -0.319645   
2019-11-19  0.071192 -0.668344  0.086140 -0.088537  0.008110  0.000293   
2019-11-18 -0.920610 -1.243206 -1.159792 -1.228155 -0.108002 -0.964755   
2019-11-15 -0.094954 -0.628694 -0.607689 -0.212857  0.197316 -0.111310   
2019-11-14  0.011797  0.119944 -0.878679 -0.883600 -0.094735 -0.198080   

                 ARE      ARNC       ATO      ATVI       AVB      AVGO  \
2019-11-20 -0.455295 -0.781324 -0.248025 -0.401843  0.347991 -0.712499   
2019-11-19 -0.113358 -0.019167  0.098219 -0.019326  0.263676 -0.236504   
2019-11-18 -1.755541 -1.275502 -0.861091 -0.625306 -2.362729 -0.829496   
2019-11-15 -0.994621 -0.159620 -0.274753  0.210387 -0.495271 -0.518456   
2019-11-14 -0.815246 -0.605540 -0.174620  0.278142 -0.157929 -0.009724   

              